# Проверка работоспособности ссылок

In [ ]:
github_token = 'input your github token'
dev_brunch = 'dev-1.8'

In [ ]:
!pip -q install fake-useragent

In [ ]:
from bs4 import BeautifulSoup
from fake_useragent import UserAgent
import requests
import base64
import json
import os
import re

headers = {}
if github_token:
    headers['Authorization'] = f"token {github_token}"

url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/?ref={dev_brunch}'
r = requests.get(url, headers=headers)
r.raise_for_status()
data = r.json()
lecture_names = [x['name'] for x in data[2:17]]

print('Get lectures links:')
all_urls = {}
for lecture in lecture_names:
    url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_brunch}'
    r = requests.get(url, headers=headers)
    r.raise_for_status()
    data = r.json()
    file_content = data['content']
    file_content_encoding = data.get('encoding')
    if file_content_encoding == 'base64':
        file_content = base64.b64decode(file_content).decode()
    file_content = json.loads(file_content)

    links_add = []
    for k in range(len(file_content["cells"])):
        cell_text = ','.join(file_content["cells"][k]['source'])
        for num, i in enumerate(cell_text):
            if len(cell_text) <= num+1:
                continue

            if (cell_text[num] == ']') and (cell_text[num+1] == '('):
                url_list = []
                mean_idx = num + 2
                start_idx = num
                end_idx = num
                while cell_text[start_idx] != '[':
                    start_idx -= 1
                while cell_text[end_idx] != ')':
                    end_idx += 1
                url_list.append(cell_text[start_idx+1:num])
                url_list.append(cell_text[mean_idx:end_idx])
                links_add.append(url_list)
    all_urls[lecture[:3]] = links_add

ua = UserAgent()
for key in all_urls.keys():
    print(f'\n****** Лекция {key} ******')
    for url in all_urls[key]:
        try:
            r = requests.get(url=url[1], headers={'user-agent': f'{ua.random}'})
        except:
            print(f"? какие то траблы, вот она {url[1]} и название {url[0]}")
        if r.status_code != 200:
            name_url = url[0]
            current_url = url[1]
            print(f'\t>>>> ссылка >>>> {name_url} вовзвращает {r.status_code} \| URL: {current_url}')




print('All links received!')
